In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchvision
import torchvision.models as models
from torchvision.models.feature_extraction import create_feature_extractor
from torch.utils.data import Dataset, DataLoader
import torch.optim.lr_scheduler
import SimpleITK as sitk
import matplotlib.pyplot as plt
from IPython.display import clear_output
import albumentations as A
from albumentations.pytorch import ToTensorV2
from tqdm import tqdm
import numpy as np
import os
import random
from PIL import Image
import cv2
import time
from lion_pytorch import Lion
import zipfile
import io

from segmentation_models.MiniUnet import MiniUnet
from segmentation_models.Unet import Unet
from segmentation_models.MaxUnet import MaxUnet
from segmentation_models.UnetPlusPlus import UnetPlusPlus
from segmentation_models.AttentionUnetPlusPlus1 import AttentionUnetPlusPlus1
from segmentation_models.AttentionUnetPlusPlus2 import AttentionUnetPlusPlus2
from segmentation_models.AttentionUnetPlusPlus3 import AttentionUnetPlusPlus3
from segmentation_models.AttentionUnetPlusPlus4 import AttentionUnetPlusPlus4
from segmentation_models.DeepLabV3Plus_MobileNetV2 import DeepLabV3Plus_MobileNetV2
from segmentation_models.CBAM_DeepLabV3Plus_MobileNetV2 import CBAM_DeepLabV3Plus_MobileNetV2
from segmentation_models.CBAM_DeepLabV3Plus_EfficientNetB0 import CBAM_DeepLabV3Plus_EfficientNetB0
from segmentation_models.MedT import MedT
from segmentation_models.TransUNet import TransUNet

DEVICE = 'cuda'

In [2]:
#Класс датасета (оптимальный для работы с разным объемом оперативной памяти, используется в проекте)
class CustomDataset(Dataset):
    def __init__(self, folder, gt_folder, size, batch, max_uses_per_scan, transforms) -> None:
        self.images = []
        self.masks = []
        self.batch = batch #количество исследований КТ, загружаемых одновременно в оперативную память
        self.max_uses_per_scan = max_uses_per_scan #сколько в среднем раз будет браться случайный срез из каждого КТ до перезагрузки в оперативную память
        self.folder = folder 
        self.gt_folder = gt_folder
        self.counter = 0
        self.size = size

        self.mapping = {0: 0, 3: 1, 4: 2, 5: 3}
        self.lookup_table = self._create_lookup_table()
        
        for fname in os.listdir(folder):
            if '.mhd' in fname:
                img_path = os.path.join(folder, fname)
                mask_path = os.path.join(gt_folder, fname)
                self.images.append(img_path)
                self.masks.append(mask_path)

        self.transform = transforms
        self.current_ct_index = 0
        self.scans = list(zip(self.images, self.masks))
        random.shuffle(self.scans)
        self.load()

    def _create_lookup_table(self):
        max_label = max(self.mapping.keys())
        lookup = np.zeros(max_label + 1, dtype=np.int64)
        for original_label, new_label in self.mapping.items():
            lookup[original_label] = new_label
        return lookup
        
    def load(self):
        if self.current_ct_index + self.batch > len(self.images):
            self.current_ct_index = 0
            random.shuffle(self.scans)

        img_filenames = self.scans[self.current_ct_index : self.current_ct_index + self.batch] #pairs

        img_pathes = [img_filename[0] for img_filename in img_filenames]
        mask_pathes = [mask_filename[1] for mask_filename in img_filenames]

        self.imgs = [sitk.ReadImage(img_path) for img_path in img_pathes]
        self.masks = [sitk.ReadImage(mask_path) for mask_path in mask_pathes]
        
        self.current_ct_index += self.batch
        self.counter = 0
        

    def __getitem__(self, index):
        if self.counter >= self.max_uses_per_scan * self.batch:
            self.load()

        index = random.randint(0, self.batch - 1)
        img = self.imgs[index]
        
        slice_num = random.randint(0, img.GetDepth()-1)
        
        img = sitk.GetArrayFromImage(img[:,:,slice_num])
        mask = sitk.GetArrayFromImage(self.masks[index][:,:,slice_num])
        
        img = img.astype(np.float32)
        img = ((img - img.min()) / (img.max() - img.min()))

        mask = self.lookup_table[mask]

        self.counter += 1

        transformed_all = self.transform(image=img, mask=mask)
        transformed_img = transformed_all['image']
        transformed_mask = transformed_all['mask']
        return transformed_img, transformed_mask

    def __len__(self):
        return self.size

In [3]:
#Функционалы потерь
class DiceLoss(nn.Module):
    def __init__(self, eps=1e-6):
        super(DiceLoss, self).__init__()
        self.eps = eps

    def forward(self, inputs, targets):
        num_classes = inputs.size(1)  #Число классов (4)

        inputs = F.softmax(inputs, dim=1) 

        targets_one_hot = F.one_hot(targets, num_classes=num_classes).permute(0, 3, 1, 2).float()

        intersection = torch.sum(inputs * targets_one_hot, dim=(2, 3)) 
        cardinality = torch.sum(inputs + targets_one_hot, dim=(2, 3))

        dice_loss = 1 - (2. * intersection + self.eps) / (cardinality + self.eps)
        loss = dice_loss.mean()

        return loss

class FocalLoss(nn.Module):
    def __init__(self, gamma=2, alpha=None, eps=1e-6):
        super(FocalLoss, self).__init__()
        self.gamma = gamma
        self.alpha = alpha 
        self.eps = eps

    def forward(self, inputs, targets):
        num_classes = inputs.size(1)

        inputs_soft = F.softmax(inputs, dim=1) + self.eps 

        targets_one_hot = F.one_hot(targets, num_classes=num_classes).permute(0, 3, 1, 2).float()  

        ce_loss = -targets_one_hot * torch.log(inputs_soft)  

        focal_loss = ce_loss * ((1 - inputs_soft) ** self.gamma)

        if self.alpha is not None:
            alpha = torch.tensor(self.alpha).to(inputs.device) 
            focal_loss = alpha.view(1, -1, 1, 1) * focal_loss 

        loss = focal_loss.mean() 

        return loss

class IOULoss(nn.Module):
    def __init__(self, eps=1e-6):
        super(IOULoss, self).__init__()
        self.eps = eps 

    def forward(self, inputs, targets):
        num_classes = inputs.size(1) 

        inputs = F.softmax(inputs, dim=1)

        targets_one_hot = F.one_hot(targets, num_classes=num_classes).permute(0, 3, 1, 2).float()

        intersection = torch.sum(inputs * targets_one_hot, dim=(2, 3)) 
        union = torch.sum(inputs + targets_one_hot - inputs * targets_one_hot, dim=(2, 3))

        iou = (intersection + self.eps) / (union + self.eps)

        iou_loss = 1 - iou
        loss = iou_loss.mean()  

        return loss

class HybridLoss(nn.Module):
    def __init__(self, weight=None):
        super(HybridLoss, self).__init__()
        self.dice_loss = DiceLoss()
        self.focal_loss = FocalLoss()
        self.iou_loss = IOULoss()
        self.weight = weight  #Список весов для каждой функции потерь

        if self.weight is None:
            #Если веса не заданы, используем равные веса
            self.weight = [1/3, 1/3, 1/3]

    def forward(self, inputs, targets):
        loss_dice = self.dice_loss(inputs, targets)
        loss_focal = self.focal_loss(inputs, targets)
        loss_iou = self.iou_loss(inputs, targets)

        #Комбинируем потери с заданными весами
        loss = self.weight[0] * loss_dice + self.weight[1] * loss_focal + self.weight[2] * loss_iou

        return loss

In [4]:
#Метрики качества
class DiceCoefficient(nn.Module):
    def __init__(self, num_classes, eps=1e-8):
        super(DiceCoefficient, self).__init__()
        self.num_classes = num_classes
        self.eps = eps

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            #Получаем предсказанные классы через argmax
            preds = torch.argmax(inputs, dim=1)
        else:
            preds = inputs
        
        dice_scores = []

        #Итерация по всем классам, кроме фона
        for cls in range(1, self.num_classes):
            pred_mask = (preds == cls).float() 
            target_mask = (targets == cls).float() 

            intersection = (pred_mask * target_mask).sum(dim=(1, 2))
            pred_sum = pred_mask.sum(dim=(1, 2))
            target_sum = target_mask.sum(dim=(1, 2))
            union = pred_sum + target_sum

            dice = (2 * intersection + self.eps) / (union + self.eps)

            dice_scores.append(dice)

        dice_scores = torch.stack(dice_scores, dim=1)

        dice_mean = dice_scores.mean()

        return dice_mean

class OneClassDiceCoefficient(nn.Module):
    def __init__(self, num_classes, class_num, eps=1e-8):
        super(OneClassDiceCoefficient, self).__init__()
        self.num_classes = num_classes
        self.eps = eps
        self.class_num = class_num

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            preds = torch.argmax(inputs, dim=1)  
        else:
            preds = inputs

        cls = self.class_num

        pred_mask = (preds == cls).float()
        target_mask = (targets == cls).float() 

        intersection = (pred_mask * target_mask).sum(dim=(1, 2))
        pred_sum = pred_mask.sum(dim=(1, 2)) 
        target_sum = target_mask.sum(dim=(1, 2))
        union = pred_sum + target_sum

        dice = torch.where(union > 0, (2 * intersection + self.eps) / (union + self.eps), torch.zeros_like(union).float())

        dice_mean = dice.mean()
        return dice_mean

class IOU(nn.Module):
    def __init__(self, num_classes, eps=1e-8):
        super(IOU, self).__init__()
        self.num_classes = num_classes
        self.eps = eps

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            preds = torch.argmax(inputs, dim=1) 
        else:
            preds = inputs

        iou_list = []
        for cls in range(1, self.num_classes):
            pred_cls = (preds == cls).float()
            target_cls = (targets == cls).float() 

            intersection = torch.sum(pred_cls * target_cls, dim=(1, 2))
            union = torch.sum(pred_cls + target_cls - pred_cls * target_cls, dim=(1, 2)) 

            iou = (intersection + self.eps) / (union + self.eps) 
            iou_list.append(iou)
            
        iou = torch.stack(iou_list, dim=1) 

        iou_mean = iou.mean()

        return iou_mean

class OneClassIOU(nn.Module):
    def __init__(self, num_classes, class_num, eps=1e-8):
        super(OneClassIOU, self).__init__()
        self.num_classes = num_classes
        self.eps = eps
        self.class_num = class_num

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            preds = torch.argmax(inputs, dim=1) 
        else:
            preds = inputs

        cls = self.class_num
        pred_cls = (preds == cls).float() 
        target_cls = (targets == cls).float() 

        intersection = torch.sum(pred_cls * target_cls, dim=(1, 2))
        union = torch.sum(pred_cls + target_cls - pred_cls * target_cls, dim=(1, 2))

        iou = torch.where(union > 0, (intersection + self.eps) / (union + self.eps), torch.zeros_like(union).float())

        iou_mean = iou.mean()
        
        return iou_mean

class PixelAccuracy(nn.Module):
    def __init__(self, ignore_index=None):
        super(PixelAccuracy, self).__init__()
        self.ignore_index = ignore_index  # Индекс класса, который следует игнорировать (фон)

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            _, preds = torch.max(inputs, dim=1) 
        else:
            preds = inputs

        if self.ignore_index is not None:
            mask = targets != self.ignore_index
            correct = (preds[mask] == targets[mask]).sum().float()
            total = mask.sum().float()
        else:
            correct = (preds == targets).sum().float()
            total = targets.numel()

        accuracy = correct / (total + 1e-8)

        return accuracy

class Precision(nn.Module):
    def __init__(self, num_classes, eps=1e-8):
        super(Precision, self).__init__()
        self.num_classes = num_classes
        self.eps = eps

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            _, preds = torch.max(inputs, dim=1) 
        else:
            preds = inputs

        precision = []
        for cls in range(1, self.num_classes):
            true_positive = ((preds == cls) & (targets == cls)).float().view(preds.size(0), -1).sum(dim=1) 
            predicted_positive = (preds == cls).float().view(preds.size(0), -1).sum(dim=1) 
            precision_cls = (true_positive + self.eps) / (predicted_positive + self.eps) 
            precision.append(precision_cls)

        precision = torch.stack(precision, dim=1) 
        precision_per_object = precision.mean(dim=1) 

        precision_mean = precision_per_object.mean()

        return precision_mean

class OneClassPrecision(nn.Module):
    def __init__(self, num_classes, class_num, eps=1e-8):
        super(OneClassPrecision, self).__init__()
        self.num_classes = num_classes
        self.eps = eps  
        self.class_num = class_num

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            _, preds = torch.max(inputs, dim=1) 
        else:
            preds = inputs

        true_positive = ((preds == self.class_num) & (targets == self.class_num)).float().view(preds.size(0), -1).sum(dim=1) 
        predicted_positive = (preds == self.class_num).float().view(preds.size(0), -1).sum(dim=1)
        precision_cls = (true_positive + self.eps) / (predicted_positive + self.eps) 

        precision_mean = precision_cls.mean()

        return precision_mean

class Recall(nn.Module):
    def __init__(self, num_classes, eps=1e-8):
        super(Recall, self).__init__()
        self.num_classes = num_classes
        self.eps = eps 

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            _, preds = torch.max(inputs, dim=1) 
        else:
            preds = inputs

        recall = []
        for cls in range(1, self.num_classes):
            true_positive = ((preds == cls) & (targets == cls)).float().view(preds.size(0), -1).sum(dim=1)
            actual_positive = (targets == cls).float().view(targets.size(0), -1).sum(dim=1)
            recall_cls = (true_positive + self.eps) / (actual_positive + self.eps) 
            recall.append(recall_cls)
        
        recall = torch.stack(recall, dim=1)
        recall_per_object = recall.mean(dim=1) 

        recall_mean = recall_per_object.mean()

        return recall_mean

class OneClassRecall(nn.Module):
    def __init__(self, num_classes, class_num, eps=1e-8):
        super(OneClassRecall, self).__init__()
        self.num_classes = num_classes
        self.eps = eps  
        self.class_num = class_num

    def forward(self, inputs, targets, use_argmax=True):
        if use_argmax:
            _, preds = torch.max(inputs, dim=1)  
        else:
            preds = inputs

        true_positive = ((preds == self.class_num) & (targets == self.class_num)).float().view(preds.size(0), -1).sum(dim=1) 
        actual_positive = (targets == self.class_num).float().view(targets.size(0), -1).sum(dim=1) 

        recall_cls = torch.where(actual_positive > 0, (true_positive + self.eps) / (actual_positive + self.eps), torch.zeros_like(actual_positive).float())

        recall_mean = recall_cls.mean()

        return recall_mean

In [5]:
DEVICE = 'cuda'
BATCH_SIZE = 8

def train_segmentation_model(model, optimizer, criterion, train_transforms, val_transforms, header, metrics, file_name, n_epoch = 101):
    """
    model - модель (экземпляр) для обучения
    optimizer - оптимизатор
    criterion - функционал ошибки
    train_transforms - аугментации для обучения
    val_transforms - аугментации для валидации/теста (обычно только Resize) 
    header - описание эксперимента, нужное для логирования (логи в segmentation_logs.txt) 
    metrics - метрики для логирования
    n_epoch - максимальное количество эпох обучения (под эпохой подразумевается не полный прогон всех данных, а только size из CustomDataset из-за ограниченных вычислительных ресурсов)
    """
    with open(file_name, 'a') as file:
       file.write(header + '\n')
    max_acc = 0
    min_loss = 100
    losses_train, losses_val = [], []

    train_dataset = CustomDataset('D:\\subset0', 'D:\\seg-lungs-LUNA16', 960, 136, 5000, train_transforms)
    train_dataloader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True)
    val_dataset = CustomDataset('D:\\subset1', 'D:\\seg-lungs-LUNA16', 128, 26, 5000, val_transforms)
    val_dataloader = DataLoader(val_dataset, batch_size=BATCH_SIZE, shuffle=True) 

    current_metrics = [0] * (2 * len(metrics))
    
    for epoch in range(1, n_epoch + 1):
        model.train()

        current_metrics = [0] * (2 * len(metrics))
        
        train_loss = 0
        for inputs, masks in tqdm(train_dataloader):
            inputs = inputs.to(DEVICE)
            masks = masks.to(DEVICE)

            optimizer.zero_grad()
            outputs = model(inputs)
            
            loss = criterion(outputs, masks.long())
            loss.backward()
            optimizer.step()
            
            train_loss += loss.item()
            for i in range(len(metrics)):
                current_metrics[i] += metrics[i][0](outputs, masks.long()).item()

        losses_train.append(train_loss / len(train_dataloader))

        model.eval()

        val_loss = 0
        val_acc = 0
        val_pixel_acc = 0
        mask_true0 = 0
        mask_true1 = 0
        mask_true2 = 0
        mask_true3 = 0
        with torch.no_grad():
            for inputs, masks in tqdm(val_dataloader):
                inputs = inputs.to(DEVICE)
                masks = masks.to(DEVICE)

                outputs = model(inputs)
                
                loss = criterion(outputs, masks.long())

                val_loss += loss.item()

                preds = torch.argmax(outputs, dim=1)
                for i in range(inputs.shape[0]):
                    mask_true0 += (masks[i] == 0).cpu().numpy().sum()
                    mask_true1 += (masks[i] == 1).cpu().numpy().sum()
                    mask_true2 += (masks[i] == 2).cpu().numpy().sum()
                    mask_true3 += (masks[i] == 3).cpu().numpy().sum()
                  
                for i in range(len(metrics)):
                    current_metrics[i + len(metrics)] += metrics[i][0](outputs, masks.long()).item()

        #print(mask_true0, mask_true1, mask_true2, mask_true3) #отладочный вывод (можно использовать для баланса классов)
        losses_val.append(val_loss / len(val_dataloader))
                
        for i in range(len(metrics)):
            current_metrics[i] = current_metrics[i] / len(train_dataloader)
            current_metrics[i + len(metrics)] = current_metrics[i + len(metrics)] / len(val_dataloader)

        out_string = f'Iteration: {epoch}\ntrain loss: {losses_train[-1]}\n'
        for i in range(len(metrics)):
            out_string += f'train {metrics[i][1]}: {current_metrics[i]}\n'
            
        out_string += f'test loss: {losses_val[-1]}\n'
        for i in range(len(metrics)):
            out_string += f'test {metrics[i][1]}: {current_metrics[i + len(metrics)]}\n'

        with open(file_name, 'a') as file:
           file.write(out_string + '\n')    

       # torch.save({
       #      'model_state_dict': model.state_dict(),
       #      'optimizer_state_dict': optimizer.state_dict()
       # }, f'mini_unet_{epoch}.pth')
       #print(out_string)

In [6]:
train_transforms = A.Compose([
    A.Resize(128, 128),
    A.Rotate(limit=3.5, p=0.7),
    ToTensorV2()
])
val_transforms = A.Compose([
    A.Resize(128, 128),
    ToTensorV2()
])  

Баланс классов (примерный)
87.1 : 5.965 : 6.836 : 0.102

In [8]:
#Обучение модели
model = AttentionUnetPlusPlus2(blocks = 64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = nn.CrossEntropyLoss()

metrics = [(PixelAccuracy(), 'pixel accuracy'), 
           (DiceCoefficient(4), 'mean dice'),
           (OneClassDiceCoefficient(4, 1), 'left lung dice'),
           (OneClassDiceCoefficient(4, 2), 'right lung dice'),
           (OneClassDiceCoefficient(4, 3), 'trachea dice'),
           (IOU(4), 'mean IOU'),
           (OneClassIOU(4, 1), 'left lung IOU'),
           (OneClassIOU(4, 2), 'right lung IOU'),
           (OneClassIOU(4, 3), 'trachea IOU'),
           (Precision(4), 'mean precision'),
           (OneClassPrecision(4, 1), 'left lung precision'),
           (OneClassPrecision(4, 2), 'right lung precision'),
           (OneClassPrecision(4, 3), 'trachea precision'),
           (Recall(4), 'mean recall'),
           (OneClassRecall(4, 1), 'left lung recall'),
           (OneClassRecall(4, 2), 'right lung recall'),
           (OneClassRecall(4, 3), 'trachea recall')]
train_segmentation_model(model, optimizer, criterion, train_transforms, val_transforms, 'AU-Net++ v2, cross-entropy loss, adam optimizer, batch size = 8, resize + rotation augmentations', metrics, 'Losses.txt', n_epoch = 100)

100%|██████████████████████████████████████████████████████████████████████████████████| 16/16 [00:05<00:00,  3.07it/s]


In [7]:
###########################################
# Функции для расчёта метрик по одному классу
###########################################
BATCH_SIZE = 8

def compute_one_class_dice(preds, targets, class_num, eps=1e-8):
    """
    Вычисляет Dice для одного класса по всем срезам, усредняя только по тем срезам, где класс присутствует в ground truth.
    preds, targets: тензоры формы (N, H, W) с целочисленными метками.
    Если ни в одном срезе объект не встречается, возвращается 0.
    """
    dice_scores = []
    N = preds.shape[0]
    for i in range(N):
        if (targets[i] == class_num).sum() > 0:
            pred_mask = (preds[i] == class_num).float()
            target_mask = (targets[i] == class_num).float()
            intersection = (pred_mask * target_mask).sum().float()
            union = pred_mask.sum() + target_mask.sum()
            dice = (2 * intersection + eps) / (union + eps)
            dice_scores.append(dice.item())
    return sum(dice_scores) / len(dice_scores) if dice_scores else 0.0

def compute_one_class_iou(preds, targets, class_num, eps=1e-8):
    """
    Вычисляет IoU для одного класса по всем срезам, усредняя только по тем срезам, где класс присутствует.
    """
    iou_scores = []
    N = preds.shape[0]
    for i in range(N):
        if (targets[i] == class_num).sum() > 0:
            pred_mask = (preds[i] == class_num).float()
            target_mask = (targets[i] == class_num).float()
            intersection = (pred_mask * target_mask).sum().float()
            union = pred_mask.sum() + target_mask.sum() - intersection
            iou = (intersection + eps) / (union + eps)
            iou_scores.append(iou.item())
    return sum(iou_scores) / len(iou_scores) if iou_scores else 0.0

def compute_one_class_precision(preds, targets, class_num):
    """
    Вычисляет Precision для одного класса по всем срезам,
    усредняя только по тем срезам, где в ground truth присутствует объект данного класса.
    Если модель не предсказала ни одного пикселя данного класса, считаем Precision = 0.
    """
    precision_scores = []
    N = preds.shape[0]
    for i in range(N):
        if (targets[i] == class_num).sum() > 0:
            pred_mask = (preds[i] == class_num)
            target_mask = (targets[i] == class_num)
            TP = ((pred_mask) & (target_mask)).sum().float()
            predicted_positive = pred_mask.sum().float()
            if predicted_positive.item() > 0:
                precision_val = (TP / predicted_positive).item()
            else:
                precision_val = 0.0
            precision_scores.append(precision_val)
    return sum(precision_scores) / len(precision_scores) if precision_scores else 0.0


def compute_one_class_recall(preds, targets, class_num):
    """
    Вычисляет Recall для одного класса по всем срезам,
    усредняя только по тем срезам, где объект данного класса есть в ground truth.
    """
    recall_scores = []
    N = preds.shape[0]
    for i in range(N):
        if (targets[i] == class_num).sum() > 0:
            pred_mask = (preds[i] == class_num)
            target_mask = (targets[i] == class_num)
            TP = ((pred_mask) & (target_mask)).sum().float()
            actual_positive = target_mask.sum().float()
            recall = TP / actual_positive
            recall_scores.append(recall.item())
    return sum(recall_scores) / len(recall_scores) if recall_scores else 0.0

def compute_pixel_accuracy(preds, targets):
    """
    Вычисляет попиксельную точность по всем срезам.
    """
    correct = (preds == targets).sum().item()
    total = targets.numel()
    return correct / (total + 1e-8)

###########################################
# Функция обучения и валидации модели
###########################################

DEVICE = 'cuda'
BATCH_SIZE = 8

def train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, header, file_name, n_epoch=101):
    """
    model          - модель сегментации (экземпляр nn.Module)
    optimizer      - оптимизатор
    criterion      - функция потерь
    train_transforms, val_transforms - наборы аугментаций (например, albumentations)
    header         - описание эксперимента (для логирования)
    file_name      - имя файла для записи логов
    n_epoch        - число эпох обучения (каждая эпоха – фиксированное число срезов из датасета)
    """
    with open(file_name, 'a') as file:
        file.write(header + '\n')
    
    # Создаём датасеты и DataLoader'ы
    train_dataset = CustomDataset('D:\\subset0', 'D:\\seg-lungs-LUNA16', 960, 136, 5000, train_transforms)
    train_dataloader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True)
    val_dataset = CustomDataset('D:\\subset1', 'D:\\seg-lungs-LUNA16', 256, 26, 5000, val_transforms)
    val_dataloader = DataLoader(val_dataset, batch_size=BATCH_SIZE, shuffle=True)
    
    for epoch in range(1, n_epoch + 1):
        ###########################################
        # Обучение: накопление предсказаний для train
        ###########################################
        model.train()
        train_loss = 0.0
        all_train_preds = []
        all_train_targets = []
        for inputs, masks in tqdm(train_dataloader, desc=f"Epoch {epoch} [train]"):
            inputs = inputs.to(DEVICE)
            masks = masks.to(DEVICE)
            
            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, masks.long())
            loss.backward()
            optimizer.step()
            train_loss += loss.item()
            
            preds = torch.argmax(outputs, dim=1).detach().cpu()
            all_train_preds.append(preds)
            all_train_targets.append(masks.cpu())
        train_loss /= len(train_dataloader)
        all_train_preds = torch.cat(all_train_preds, dim=0)  # Форма (N, H, W)
        all_train_targets = torch.cat(all_train_targets, dim=0)
        
        # Расчёт метрик для train
        train_pixel_acc = compute_pixel_accuracy(all_train_preds, all_train_targets)
        
        train_dice_left = compute_one_class_dice(all_train_preds, all_train_targets, class_num=1)
        train_dice_right = compute_one_class_dice(all_train_preds, all_train_targets, class_num=2)
        train_dice_trachea = compute_one_class_dice(all_train_preds, all_train_targets, class_num=3)
        train_mean_dice = (train_dice_left + train_dice_right + train_dice_trachea) / 3.0

        train_iou_left = compute_one_class_iou(all_train_preds, all_train_targets, class_num=1)
        train_iou_right = compute_one_class_iou(all_train_preds, all_train_targets, class_num=2)
        train_iou_trachea = compute_one_class_iou(all_train_preds, all_train_targets, class_num=3)
        train_mean_iou = (train_iou_left + train_iou_right + train_iou_trachea) / 3.0

        train_precision_left = compute_one_class_precision(all_train_preds, all_train_targets, class_num=1)
        train_precision_right = compute_one_class_precision(all_train_preds, all_train_targets, class_num=2)
        train_precision_trachea = compute_one_class_precision(all_train_preds, all_train_targets, class_num=3)
        train_mean_precision = (train_precision_left + train_precision_right + train_precision_trachea) / 3.0

        train_recall_left = compute_one_class_recall(all_train_preds, all_train_targets, class_num=1)
        train_recall_right = compute_one_class_recall(all_train_preds, all_train_targets, class_num=2)
        train_recall_trachea = compute_one_class_recall(all_train_preds, all_train_targets, class_num=3)
        train_mean_recall = (train_recall_left + train_recall_right + train_recall_trachea) / 3.0

        ###########################################
        # Валидация: накопление предсказаний для test
        ###########################################
        model.eval()
        val_loss = 0.0
        all_val_preds = []
        all_val_targets = []
        with torch.no_grad():
            for inputs, masks in tqdm(val_dataloader, desc=f"Epoch {epoch} [val]"):
                inputs = inputs.to(DEVICE)
                masks = masks.to(DEVICE)
                outputs = model(inputs)
                loss = criterion(outputs, masks.long())
                val_loss += loss.item()
                
                preds = torch.argmax(outputs, dim=1).detach().cpu()
                all_val_preds.append(preds)
                all_val_targets.append(masks.cpu())
        val_loss /= len(val_dataloader)
        all_val_preds = torch.cat(all_val_preds, dim=0)
        all_val_targets = torch.cat(all_val_targets, dim=0)
        
        # Расчёт метрик для test
        val_pixel_acc = compute_pixel_accuracy(all_val_preds, all_val_targets)
        
        val_dice_left = compute_one_class_dice(all_val_preds, all_val_targets, class_num=1)
        val_dice_right = compute_one_class_dice(all_val_preds, all_val_targets, class_num=2)
        val_dice_trachea = compute_one_class_dice(all_val_preds, all_val_targets, class_num=3)
        val_mean_dice = (val_dice_left + val_dice_right + val_dice_trachea) / 3.0

        val_iou_left = compute_one_class_iou(all_val_preds, all_val_targets, class_num=1)
        val_iou_right = compute_one_class_iou(all_val_preds, all_val_targets, class_num=2)
        val_iou_trachea = compute_one_class_iou(all_val_preds, all_val_targets, class_num=3)
        val_mean_iou = (val_iou_left + val_iou_right + val_iou_trachea) / 3.0

        val_precision_left = compute_one_class_precision(all_val_preds, all_val_targets, class_num=1)
        val_precision_right = compute_one_class_precision(all_val_preds, all_val_targets, class_num=2)
        val_precision_trachea = compute_one_class_precision(all_val_preds, all_val_targets, class_num=3)
        val_mean_precision = (val_precision_left + val_precision_right + val_precision_trachea) / 3.0

        val_recall_left = compute_one_class_recall(all_val_preds, all_val_targets, class_num=1)
        val_recall_right = compute_one_class_recall(all_val_preds, all_val_targets, class_num=2)
        val_recall_trachea = compute_one_class_recall(all_val_preds, all_val_targets, class_num=3)
        val_mean_recall = (val_recall_left + val_recall_right + val_recall_trachea) / 3.0

        ###########################################
        # Логирование результатов в файл
        ###########################################
        out_string = f"Iteration: {epoch}\n"
        out_string += f"Train loss: {train_loss:.4f}\n"
        out_string += f"Train pixel accuracy: {train_pixel_acc:.4f}\n"
        out_string += f"Train left lung dice: {train_dice_left:.4f}\n"
        out_string += f"Train right lung dice: {train_dice_right:.4f}\n"
        out_string += f"Train trachea dice: {train_dice_trachea:.4f}\n"
        out_string += f"Train mean dice: {train_mean_dice:.4f}\n"
        out_string += f"Train left lung IoU: {train_iou_left:.4f}\n"
        out_string += f"Train right lung IoU: {train_iou_right:.4f}\n"
        out_string += f"Train trachea IoU: {train_iou_trachea:.4f}\n"
        out_string += f"Train mean IoU: {train_mean_iou:.4f}\n"
        out_string += f"Train left lung precision: {train_precision_left:.4f}\n"
        out_string += f"Train right lung precision: {train_precision_right:.4f}\n"
        out_string += f"Train trachea precision: {train_precision_trachea:.4f}\n"
        out_string += f"Train mean precision: {train_mean_precision:.4f}\n"
        out_string += f"Train left lung recall: {train_recall_left:.4f}\n"
        out_string += f"Train right lung recall: {train_recall_right:.4f}\n"
        out_string += f"Train trachea recall: {train_recall_trachea:.4f}\n"
        out_string += f"Train mean recall: {train_mean_recall:.4f}\n"
        out_string += f"----------------------------------------\n"
        out_string += f"Test loss: {val_loss:.4f}\n"
        out_string += f"Test pixel accuracy: {val_pixel_acc:.4f}\n"
        out_string += f"Test left lung dice: {val_dice_left:.4f}\n"
        out_string += f"Test right lung dice: {val_dice_right:.4f}\n"
        out_string += f"Test trachea dice: {val_dice_trachea:.4f}\n"
        out_string += f"Test mean dice: {val_mean_dice:.4f}\n"
        out_string += f"Test left lung IoU: {val_iou_left:.4f}\n"
        out_string += f"Test right lung IoU: {val_iou_right:.4f}\n"
        out_string += f"Test trachea IoU: {val_iou_trachea:.4f}\n"
        out_string += f"Test mean IoU: {val_mean_iou:.4f}\n"
        out_string += f"Test left lung precision: {val_precision_left:.4f}\n"
        out_string += f"Test right lung precision: {val_precision_right:.4f}\n"
        out_string += f"Test trachea precision: {val_precision_trachea:.4f}\n"
        out_string += f"Test mean precision: {val_mean_precision:.4f}\n"
        out_string += f"Test left lung recall: {val_recall_left:.4f}\n"
        out_string += f"Test right lung recall: {val_recall_right:.4f}\n"
        out_string += f"Test trachea recall: {val_recall_trachea:.4f}\n"
        out_string += f"Test mean recall: {val_mean_recall:.4f}\n"
        out_string += f"========================================\n"
        
        with open(file_name, 'a') as file:
            file.write(out_string + '\n')
        
        # (Опционально) можно сохранять модель по эпохам
        # torch.save({
        #     'model_state_dict': model.state_dict(),
        #     'optimizer_state_dict': optimizer.state_dict(),
        # }, f'mini_unet_epoch_{epoch}.pth')

In [7]:
nets = [MiniUnet(), Unet(), MaxUnet(), UnetPlusPlus(), AttentionUnetPlusPlus1(),
         AttentionUnetPlusPlus2(), AttentionUnetPlusPlus3(), AttentionUnetPlusPlus4(),
         DeepLabV3Plus_MobileNetV2(), CBAM_DeepLabV3Plus_MobileNetV2(), CBAM_DeepLabV3Plus_EfficientNetB0(),
         MedT(), TransUNet()]

for model in nets:
    print(type(model).__name__, ': ', "{:,}".format(sum(p.numel() for p in model.parameters())).replace(',', "'"))

MiniUnet :  1'273'860
Unet :  31'042'564
MaxUnet :  162'140'164
UnetPlusPlus :  32'494'916
AttentionUnetPlusPlus1 :  33'020'528
AttentionUnetPlusPlus2 :  33'020'788
AttentionUnetPlusPlus3 :  39'370'100
AttentionUnetPlusPlus4 :  56'080'436
DeepLabV3Plus_MobileNetV2 :  13'940'130
CBAM_DeepLabV3Plus_MobileNetV2 :  13'957'322
CBAM_DeepLabV3Plus_EfficientNetB0 :  15'740'998
MedT :  17'209'864
TransUNet :  135'981'832


In [8]:
model = MiniUnet(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MiniUnet(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:08<00:00,  3.92it/s]


In [9]:
model = MiniUnet(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MiniUnet(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:08<00:00,  3.65it/s]


In [10]:
model = MiniUnet(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MiniUnet(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.18it/s]


In [11]:
model = MiniUnet(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MiniUnet(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.18it/s]


In [12]:
model = MiniUnet(blocks=128).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MiniUnet(128), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.26it/s]


In [13]:
model = Unet(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "Unet(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:08<00:00,  3.87it/s]


In [14]:
model = Unet(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "Unet(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.43it/s]


In [15]:
model = Unet(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "Unet(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.11it/s]


In [16]:
model = Unet(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "Unet(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.10it/s]


In [8]:
model = Unet(blocks=128).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "Unet(128), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.07it/s]


In [9]:
model = MaxUnet(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MaxUnet(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:08<00:00,  3.83it/s]


In [10]:
model = MaxUnet(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MaxUnet(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.49it/s]


In [8]:
model = MaxUnet(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MaxUnet(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.17it/s]


In [9]:
model = MaxUnet(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MaxUnet(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.32it/s]


In [10]:
model = MaxUnet(blocks=128).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MaxUnet(128), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:34<00:00,  1.09s/it]


In [11]:
model = UnetPlusPlus(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "UnetPlusPlus(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.18it/s]


In [12]:
model = UnetPlusPlus(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "UnetPlusPlus(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.16it/s]


In [13]:
model = UnetPlusPlus(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "UnetPlusPlus(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.28it/s]


In [14]:
model = UnetPlusPlus(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "UnetPlusPlus(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.11it/s]


In [8]:
model = AttentionUnetPlusPlus1(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus1(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.20it/s]


In [9]:
model = AttentionUnetPlusPlus1(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus1(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.31it/s]


In [10]:
model = AttentionUnetPlusPlus1(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus1(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.21it/s]


In [11]:
model = AttentionUnetPlusPlus1(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus1(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.04it/s]


In [12]:
model = AttentionUnetPlusPlus2(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus2(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.18it/s]


In [13]:
model = AttentionUnetPlusPlus2(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus2(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.42it/s]


In [14]:
model = AttentionUnetPlusPlus2(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus2(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.20it/s]


In [15]:
model = AttentionUnetPlusPlus2(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus2(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.08it/s]


In [16]:
model = AttentionUnetPlusPlus3(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus3(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.20it/s]


In [17]:
model = AttentionUnetPlusPlus3(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus3(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.11it/s]


In [18]:
model = AttentionUnetPlusPlus3(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus3(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.05it/s]


In [19]:
model = AttentionUnetPlusPlus3(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus3(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.07it/s]


In [20]:
model = AttentionUnetPlusPlus4(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus4(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.12it/s]


In [21]:
model = AttentionUnetPlusPlus4(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus4(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.14it/s]


In [22]:
model = AttentionUnetPlusPlus4(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus4(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.05it/s]


In [23]:
model = AttentionUnetPlusPlus4(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "AttentionUnetPlusPlus4(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  2.96it/s]


In [24]:
model = DeepLabV3Plus_MobileNetV2().to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "DeepLabV3Plus_MobileNetV2, Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.20it/s]


In [25]:
model = CBAM_DeepLabV3Plus_MobileNetV2().to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "CBAM_DeepLabV3Plus_MobileNetV2, Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.15it/s]


In [26]:
model = CBAM_DeepLabV3Plus_EfficientNetB0().to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "CBAM_DeepLabV3Plus_EfficientNetB0, Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.10it/s]


In [27]:
model = MedT(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MedT(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.54it/s]


In [28]:
model = MedT(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MedT(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.17it/s]


In [29]:
model = MedT(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MedT(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.12it/s]


In [30]:
model = MedT(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MedT(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.17it/s]


In [31]:
model = MedT(blocks=128).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "MedT(128), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.05it/s]


In [32]:
model = TransUNet(blocks=8).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "TransUNet(8), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.43it/s]


In [33]:
model = TransUNet(blocks=16).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "TransUNet(16), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.04it/s]


In [34]:
model = TransUNet(blocks=32).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "TransUNet(32), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:09<00:00,  3.21it/s]


In [35]:
model = TransUNet(blocks=64).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "TransUNet(64), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.16it/s]


In [36]:
model = TransUNet(blocks=128).to(DEVICE)
optimizer = torch.optim.Adam(model.parameters())
criterion = FocalLoss()

train_segmentation_model_2(model, optimizer, criterion, train_transforms, val_transforms, "TransUNet(128), Focal Loss, adam optimizer, batch size = 8, resize + rotation augmentations, parameters count: " + str(sum(p.numel() for p in model.parameters())), "Architectures.txt", n_epoch=200)

Epoch 200 [val]: 100%|█████████████████████████████████████████████████████████████████| 32/32 [00:10<00:00,  3.08it/s]
